# COVID-19 at CA prisons

### Import Python tools and Jupyter configuration

In [2]:
%load_ext lab_black

In [3]:
import pandas as pd
import geopandas as gpd
import datetime as dt
import matplotlib.pyplot as plt
import altair as alt

In [25]:
pd.options.display.max_columns = 100
pd.options.display.max_rows = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

### Read the raw data from a URL

In [43]:
url = "https://raw.githubusercontent.com/datadesk/california-coronavirus-data/master/cdcr-prison-totals.csv"

In [44]:
df = pd.read_csv(url)

In [45]:
src.columns = (
    src.columns.str.lower()
    .str.replace(":", "", regex=False)
    .str.replace(" ", "_", regex=False)
    .str.replace("#", "_no", regex=False)
)

In [46]:
src.dtypes

date                    object
code                    object
name                    object
city                    object
county                  object
fips                     int64
zipcode                  int64
x                      float64
y                      float64
confirmed_cases          int64
new_confirmed_cases    float64
active_cases           float64
released_cases           int64
resolved_cases         float64
deaths                   int64
new_deaths             float64
dtype: object

### Dates

In [47]:
src["date"] = pd.to_datetime(src["date"], format="%Y-%m-%d")
src["date"] = pd.to_datetime(src["date"].dt.strftime("%Y-%m-%d"))
src["year"] = src["date"].dt.year
src["quarter"] = src["date"].dt.quarter
src["day"] = src["date"].dt.day
src["month"] = src["date"].dt.month
src["weekday"] = src["date"].dt.weekday
src["monthname"] = src["date"].dt.month_name()
src["month_year_full"] = src["date"].apply(lambda x: x.strftime("%B-%Y"))
src["month_year_full"] = pd.to_datetime(src["month_year_full"])

---

In [48]:
df = src.copy()

In [51]:
df[df["name"] == "Folsom State Prison"].sort_values("date", ascending=False).head()

date code                 name     city      county  fips  \
10185 2021-06-15  FSP  Folsom State Prison  Represa  Sacramento    67   
10184 2021-06-14  FSP  Folsom State Prison  Represa  Sacramento    67   
10183 2021-06-13  FSP  Folsom State Prison  Represa  Sacramento    67   
10182 2021-06-12  FSP  Folsom State Prison  Represa  Sacramento    67   
10181 2021-06-11  FSP  Folsom State Prison  Represa  Sacramento    67   

       zipcode           x          y  confirmed_cases  new_confirmed_cases  \
10185    95671 -121.162429  38.694558             1369                  0.0   
10184    95671 -121.162429  38.694558             1369                  0.0   
10183    95671 -121.162429  38.694558             1369                  0.0   
10182    95671 -121.162429  38.694558             1369                  0.0   
10181    95671 -121.162429  38.694558             1369                  0.0   

       active_cases  released_cases  resolved_cases  deaths  new_deaths  year  \
10185           0.0              12          1355.0       2         0.0  2021   
10184           0.0              12          1355.0       2         0.0  2021   
10183           NaN              12             NaN       2         0.0  2021   
10182           NaN              12             NaN       2         0.0  2021   
10181           NaN              12             NaN       2         0.0  2021   

       quarter  day  month  weekday monthname month_year_full  
10185        2   15      6        1      June      2021-06-01  
10184        2   14      6        0      June      2021-06-01  
10183        2   13      6        6      June      2021-06-01  
10182        2   12      6        5      June      2021-06-01  
10181        2   11      6        4      June      2021-06-01

In [52]:
alt.Chart(df).mark_line().encode(
    x="date",
    y="confirmed_cases",
    color="name",
    #     facet=alt.Facet("institutionname", columns=5)
).properties(width=1000, height=600)

alt.Chart(...)

---

### Institution reports

In [117]:
from bs4 import BeautifulSoup
import requests

In [118]:
prison_url = (
    "https://www.cdcr.ca.gov/research/monthly-total-population-report-archive-2019/"
)

In [126]:
from bs4 import BeautifulSoup
import urllib.request

parser = "html.parser"
resp = urllib.request.urlopen(
    "https://www.cdcr.ca.gov/research/monthly-total-population-report-archive-2019/"
)
soup = BeautifulSoup(resp, parser, from_encoding=resp.info().get_param("charset"))

for link in soup.find_all(
    "a", href=lambda href: href and "/research/wp-content/uploads/" in href
):
    print(link["href"])

https://www.cdcr.ca.gov/research/wp-content/uploads/sites/174/2019/06/Tpop1d1901.pdf
https://www.cdcr.ca.gov/research/wp-content/uploads/sites/174/2019/06/Tpop1d1902.pdf
https://www.cdcr.ca.gov/research/wp-content/uploads/sites/174/2019/06/Tpop1d1903.pdf
https://www.cdcr.ca.gov/research/wp-content/uploads/sites/174/2019/06/Tpop1d1904.pdf
https://www.cdcr.ca.gov/research/wp-content/uploads/sites/174/2019/06/Tpop1d1905.pdf
/research/wp-content/uploads/sites/174/2019/07/Tpop1d1906.pdf
/research/wp-content/uploads/sites/174/2019/08/Tpop1d1907.pdf
/research/wp-content/uploads/sites/174/2019/09/Tpop1d1908.pdf
/research/wp-content/uploads/sites/174/2019/10/Tpop1d1909.pdf
/research/wp-content/uploads/sites/174/2019/11/Tpop1d1910.pdf
/research/wp-content/uploads/sites/174/2019/12/Tpop1d1911.pdf
/research/wp-content/uploads/sites/174/2020/01/Tpop1d1912.pdf
/research/wp-content/uploads/sites/174/2020/02/Tpop1d2001.pdf
/research/wp-content/uploads/sites/174/2020/05/Tpop1d2002.pdf
https://www.cdcr.

In [107]:
pop_df = pd.read_fwf(
    "input/prisonpop/Tpop1d2003.txt",
    skiprows=12,
    header=0,
    skipfooter=5,
    names=["name", "inmates", "designed_capacity", "pct_occupied", "staffed_capacity"],
)

In [108]:
pop_df["inmates"] = pop_df["inmates"].str.replace(",", "", regex=False)
pop_df["designed_capacity"] = pop_df["designed_capacity"].str.replace(
    ",", "", regex=False
)
pop_df["staffed_capacity"] = pop_df["staffed_capacity"].str.replace(
    ",", "", regex=False
)

In [109]:
pop_df[["name", "abbr"]] = (
    pop_df["name"].str.split("(", expand=True).replace(")", "", regex=False)
)

In [110]:
pop_df["abbr"] = pop_df["abbr"].str.replace(")", "", regex=False)

In [111]:
pop_df.tail(10)

name inmates designed_capacity  \
29          Salinas Valley State Prison     2930              2452   
30                  Valley State Prison     3024              1980   
31                   Wasco State Prison     4359              2984   
32                            Male Total  112052             85858   
33                   Female Institutions     NaN               NaN   
34  Central California Women's Facility     2795              2004   
35     California Institution for Women     1650              1398   
36                  Folsom State Prison      389               403   
37                          Female Total    4834              3805   
38                     Institution Total  116886             89663   

    pct_occupied staffed_capacity  abbr  
29         119.5             3509  SVSP  
30         152.7             2954   VSP  
31         146.1             4447   WSP  
32         130.5           118500  None  
33           NaN              NaN  None  
34         139.5             2988  CCWF  
35         118.0             1877   CIW  
36          96.5              530   FOL  
37         127.0             5395  None  
38         130.4           123895  None

In [112]:
to_drop = ["Male Total", "Female Institutions", "Female Total", "Institution Total"]

In [113]:
for t in to_drop:
    pop_df = pop_df[pop_df["name"] != t]

In [114]:
pop_df

name inmates designed_capacity  \
0                             Avenal State Prison     4294              2920   
1                         Calipatria State Prison     3055              2308   
2                  California Correctional Center     4309              3883   
3             California Correctional Institution     3666              2783   
4                          Centinela State Prison     3385              2308   
5      California Health Care Facility - Stockton     2834              2951   
6                  California Institution for Men     3515              2976   
7                         California Men's Colony     3823              3838   
8                     California Medical Facility     2475              2361   
9               California State Prison, Corcoran     2819              3116   
10               California Rehabilitation Center     4015              2491   
11                 Correctional Training Facility     5096              3312   
12                Chuckawalla Valley State Prison     2948              1738   
13                   Deuel Vocational Institution     1910              1681   
14                            Folsom State Prison     2818              2066   
15                       High Desert State Prison     3352              2324   
16                          Ironwood State Prison     2819              2200   
17                       Kern Valley State Prison     3602              2448   
18    California State Prison, Los Angeles County     3220              2300   
19                        Mule Creek State Prison     4003              3284   
20                        North Kern State Prison     3866              2694   
21                       Pelican Bay State Prison     2677              2380   
22                   Pleasant Valley State Prison     3169              2308   
23               RJ Donovan Correctional Facility     3873              2992   
24            California State Prison, Sacramento     2417              1828   
25  California Substance Abuse Treatment Facility     5278              3424   
26                     Sierra Conservation Center     4334              3836   
27                California State Prison, Solano     4179              2610   
28                       San Quentin State Prison     3988              3082   
29                    Salinas Valley State Prison     2930              2452   
30                            Valley State Prison     3024              1980   
31                             Wasco State Prison     4359              2984   
34            Central California Women's Facility     2795              2004   
35               California Institution for Women     1650              1398   
36                            Folsom State Prison      389               403   

    pct_occupied staffed_capacity  abbr  
0          147.1             4387   ASP  
1          132.4             3451   CAL  
2          111.0             4752   CCC  
3          131.7             4085   CCI  
4          146.7             3446   CEN  
5           96.0             2951  CHCF  
6          118.1             4226   CIM  
7           99.6             4407   CMC  
8          104.8             2861   CMF  
9           90.5             4476   COR  
10         161.2             3084   CRC  
11         153.9             4887   CTF  
12         169.6             2578  CVSP  
13         113.6             2190   DVI  
14         136.4             2986   FOL  
15         144.2             3461  HDSP  
16         128.1             3300   ISP  
17         147.1             3622  KVSP  
18         140.0             3400   LAC  
19         121.9             4105  MCSP  
20         143.5             4011  NKSP  
21         112.5             3361  PBSP  
22         137.3             3433  PVSP  
23         129.4             4038   RJD  
24         132.2             2545   SAC  
25         154.1             5111  SATF  
26         113.0             45